### Global Fishing Watch

**Links for inspiration:** 
+ https://docs.dask.org/en/latest/array-creation.html
+ https://examples.dask.org/machine-learning/torch-prediction.html
+ https://medium.com/mindorks/speeding-up-text-pre-processing-using-dask-45cc3ede1366

In [1]:
from dask.distributed import Client

client = Client()
client

<Client: 'tcp://127.0.0.1:37747' processes=4 threads=12, memory=16.69 GB>

In [23]:
import glob
import dask.dataframe as dd
import pandas as pd
pd.options.display.max_columns = None
pd.options.display.max_rows = None

import numpy as np

import warnings
warnings.filterwarnings('ignore')

from ipywidgets import widgets
from mpl_toolkits.basemap import Basemap
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.patches import Polygon


import timeit
start_time = timeit.default_timer()

from sklearn.datasets import fetch_species_distributions
import numpy as np
import matplotlib.pyplot as plt
from mpl_toolkits.basemap import Basemap
from sklearn.datasets.species_distributions import construct_grids
from sklearn.neighbors import KernelDensity
from sklearn.datasets.base import Bunch


from shapely.geometry import Point
from shapely.geometry import MultiLineString,mapping
from shapely.ops import polygonize
import geopandas as gpd
# from sklearn.datasets import fetch_species_distributions
# data = fetch_species_distributions()
from h3 import h3

In [78]:
RESOLUTION = 7 

In [3]:
def gfwDataNew():
    csvs = 'Fishing_By_Vessel/2018/*.csv'
    All_GFW_Grid = dd.read_csv(csvs)
    
    All_GFW_Grid.lat_bin = All_GFW_Grid.lat_bin / 10
    All_GFW_Grid.lon_bin = All_GFW_Grid.lon_bin / 10
    
    return All_GFW_Grid 

In [4]:
All_GFW_Grid = gfwDataNew()
mask = ((All_GFW_Grid['date'] >= '2018-08-02') & 
        (All_GFW_Grid['date'] <= '2018-12-28' ))
All_GFW_Grid = All_GFW_Grid.loc[mask]

In [5]:
len(All_GFW_Grid.index)

8188229

In [6]:
All_GFW_Grid.compute().head()

date  lat_bin  lon_bin       mmsi  fishing_hours
0  2018-08-02 00:00:00 UTC      0.0     67.5  416768000       0.754444
1  2018-08-02 00:00:00 UTC      0.0     67.6  416768000       0.642778
2  2018-08-02 00:00:00 UTC      0.0     67.4  416768000       0.430694
3  2018-08-02 00:00:00 UTC      0.0    159.4  933621003       4.899861
4  2018-08-02 00:00:00 UTC      0.0    159.4  933621005       1.485278

In [31]:
h3.geo_to_h3(0.0, 67.5, 7)

'87855c26effffff'

In [25]:
h3.geo_to_h3??

### Beneath the Waves

In [7]:
Beneath_The_Waves_Sensor = dd.read_csv('Beneath_The_Waves/Beneath_The_Waves.csv')

In [8]:
Beneath_The_Waves_Sensor = Beneath_The_Waves_Sensor.dropna(how='all')
Beneath_The_Waves_Sensor = Beneath_The_Waves_Sensor.dropna(subset=['Loc. date'])
Beneath_The_Waves_Sensor['Loc. date'] = dd.to_datetime(Beneath_The_Waves_Sensor['Loc. date'])
Beneath_The_Waves_Sensor = Beneath_The_Waves_Sensor.set_index('Loc. date')
#Beneath_The_Waves_Sensor.index = Beneath_The_Waves_Sensor.index.floor('D')
#Beneath_The_Waves_Sensor.index = Beneath_The_Waves_Sensor.index.tz_localize('America/Los_Angeles')
#Beneath_The_Waves_Sensor.index = Beneath_The_Waves_Sensor.index.floor('D')
Beneath_The_Waves_Sensor.head(2)

DeployID  Shark ID  Prg No.  Latitude  Longitude  \
Loc. date                                                               
2018-08-02 23:40:00       NaN    176750     6328  52.09686  -18.56774   
2018-08-02 23:40:00       NaN    176750     6328  52.09686  -18.56774   

                    Loc. quality Loc. type  Altitude  Pass Sat.  Mote Id  \
Loc. date                                                                  
2018-08-02 23:40:00            A     Argos       0.0   407   MA      NaN   
2018-08-02 23:40:00            A     Argos       0.0   407   MA      NaN   

                       Frequency      Msg Date  Comp.  Msg  > - 120 DB  \
Loc. date                                                                
2018-08-02 23:40:00  401677346.1  8/2/18 23:36      1    3           0   
2018-08-02 23:40:00  401677346.1  8/2/18 23:42      1    3           0   

                     Best level  Delta freq.   Long. 1  Lat. sol. 1   Long. 2  \
Loc. date                                                                       
2018-08-02 23:40:00        -127  401677346.1 -18.56774     52.09686 -69.77233   
2018-08-02 23:40:00        -127  401677346.1 -18.56774     52.09686 -69.77233   

                     Lat. sol. 2  Loc. idx  Nopc  Error radius  \
Loc. date                                                        
2018-08-02 23:40:00     42.22084       0.0   0.0           0.0   
2018-08-02 23:40:00     42.22084       0.0   0.0           0.0   

                     Semi-major axis  Semi-minor axis  Ellipse orientation  \
Loc. date                                                                    
2018-08-02 23:40:00              0.0              0.0                173.0   
2018-08-02 23:40:00              0.0              0.0                173.0   

                       GDOP  SENSOR #01  SENSOR #02  SENSOR #03  SENSOR #04  \
Loc. date                                                                     
2018-08-02 23:40:00  1777.0          84          71           1         NaN   
2018-08-02 23:40:00  1777.0         103         137           0         NaN   

                     SENSOR #05  SENSOR #06  SENSOR #07  SENSOR #08  \
Loc. date                                                             
2018-08-02 23:40:00         NaN         NaN         NaN         NaN   
2018-08-02 23:40:00         NaN         NaN         NaN         NaN   

                     SENSOR #09  SENSOR #10  SENSOR #11  SENSOR #12  \
Loc. date                                                             
2018-08-02 23:40:00         NaN         NaN         NaN         NaN   
2018-08-02 23:40:00         NaN         NaN         NaN         NaN   

                     SENSOR #13  SENSOR #14  SENSOR #15  SENSOR #16  \
Loc. date                                                             
2018-08-02 23:40:00         NaN         NaN         NaN         NaN   
2018-08-02 23:40:00         NaN         NaN         NaN         NaN   

                     SENSOR #17  SENSOR #18  SENSOR #19  SENSOR #20  \
Loc. date                                                             
2018-08-02 23:40:00         NaN         NaN         NaN         NaN   
2018-08-02 23:40:00         NaN         NaN         NaN         NaN   

                     SENSOR #21  SENSOR #22  SENSOR #23  SENSOR #24  \
Loc. date                                                             
2018-08-02 23:40:00         NaN         NaN         NaN         NaN   
2018-08-02 23:40:00         NaN         NaN         NaN         NaN   

                     SENSOR #25  SENSOR #26  SENSOR #27  SENSOR #28  \
Loc. date                                                             
2018-08-02 23:40:00         NaN         NaN         NaN         NaN   
2018-08-02 23:40:00         NaN         NaN         NaN         NaN   

                     SENSOR #29  SENSOR #30  SENSOR #31  SENSOR #32  
Loc. date                                                            
2018-08-02 23:40:00         NaN         NaN         NaN 

In [69]:
Beneath_the_Waves = dd.read_csv('Beneath_The_Waves/Gallagher_BTW_Tracks.csv')
Beneath_the_Waves['dt'] = dd.to_datetime(Beneath_the_Waves['dt'])
Beneath_the_Waves = Beneath_the_Waves.set_index('dt')

In [70]:
Beneath_the_Waves.head(2)

ptt        lat        lon class  Unnamed: 5
dt                                                        
2015-10-13  141268  41.575000 -69.422633     3         NaN
2015-10-13  141261  41.321267 -69.275833     3         NaN

In [63]:
Beneath_The_Waves = Beneath_the_Waves.dropna(subset=['lat', 'lon'])

In [64]:
len(Beneath_The_Waves.index)

15106

In [9]:
start_btw = Beneath_The_Waves_Sensor.index.min().compute()
end_btw = Beneath_The_Waves_Sensor.index.max().compute()

In [10]:
print(start_btw, '-', end_btw)

2018-08-02 23:40:00 - 2018-12-28 00:26:00


In [11]:
len(Beneath_The_Waves_Sensor.index)

1522

### Select Part of Globe and Plot Heatmap

In [12]:
lat = widgets.IntRangeSlider(value=[-90, 90],
    min=-90,
    max=90,
    step=1,
    description='Latitude:',
    disabled=False,
    continuous_update=True,
    orientation='horizontal',
    readout=True,
)

lon = widgets.IntRangeSlider(
    value=[-180, 180],
    min=-180,
    max=180,
    step=1,
    description='Longitude:',
    disabled=False,
    continuous_update=True,
    orientation='horizontal',
    readout=True,
)

ui = widgets.HBox([lat, lon])

def draw_screen_poly( lats, lons, m):
        x, y = m( lons, lats )
        xy = zip(x, y)
        poly = Polygon( list(xy), facecolor='red', alpha=0.4 )
        plt.gca().add_patch(poly)
        
def f(lat, lon):

    # Map Boundaries
    max_lon = lon[1]#; print("Max Longitude: ", max_lon)
    min_lon = lon[0]#; print("Min Longitude: ", min_lon)
    max_lat = lat[1]#; print("Max Latitude: ", max_lat)
    min_lat = lat[0]#; print("Min Latitude: ", min_lat)

    lats = [ min_lat, max_lat, max_lat, min_lat ]
    lons = [ min_lon, min_lon, max_lon, max_lon ]

    m = Basemap(projection='cyl',lon_0=0)
    m.drawcoastlines()
    m.drawmapboundary()
    draw_screen_poly( lats, lons, m )
    
    print('('+str(lat)+'),('+str(lon)+')')
    plt.show()
    

out = widgets.interactive_output(f, {'lat': lat, 'lon': lon})

display(ui, out)

Output()

In [14]:
### Detached fetch_species_distribution()
bandwidth = 0.36

# Map Boundaries
latlon = eval(out.outputs[0]['text'].rstrip())
max_lon = latlon[1][1]; print("Max Longitude: ", latlon[1][1])
min_lon = latlon[1][0]; print("Min Longitude: ", latlon[1][0])
max_lat = latlon[0][1]; print("Max Latitude: ", latlon[0][1])
min_lat = latlon[0][0]; print("Min Latitude: ", latlon[0][0])

Max Longitude:  180
Min Longitude:  -180
Max Latitude:  90
Min Latitude:  -90


# Geodataframe based grids and occurance of vessels in those grids

Let's divide the map in to grid of 180 latitudes and 360 longitudes

In [15]:
all_lats = np.linspace(min_lat,max_lat, 180)
all_lons = np.linspace(min_lon,max_lon, 360)
llons, llats = np.meshgrid(all_lons, all_lats)

## Let's take the points and generate a list of all the lines that will make up the polygon edges for all the grids

In [16]:
h1 = [((x1, yi), (x2, yi)) for x1, x2 in zip(all_lons[:-1], all_lons[1:]) for yi in all_lats]
v1 = [((xi, y1), (xi, y2)) for y1, y2 in zip(all_lats[:-1], all_lats[1:]) for xi in all_lons]

In [17]:
grids = list(polygonize(MultiLineString(h1 + v1)))

## Generate a geodf calles gridsgdf that has all the polygons corresponding to the grids

In [18]:
gridsgdf = gpd.GeoDataFrame(grids)
crs = {'init': 'epsg:4326'}
gridsgdf.crs=crs
gridsgdf = gridsgdf.rename(columns={0:'polygeo'}).set_geometry('polygeo')

In [19]:
gridsgdf.head(2)

polygeo
0  POLYGON ((-178.9972144846797 -90, -180 -90, -1...
1  POLYGON ((-178.9972144846797 -88.9944134078212...

## Position locations from GFW to center of the GFW 'bins' which are 0.05 x 0.05 in degrees

In [20]:
All_GFW_Grid['lat_centroid'] = All_GFW_Grid.loc[:]['lat_bin'] + 0.05
All_GFW_Grid['lon_centroid'] = All_GFW_Grid.loc[:]['lon_bin'] + 0.05

In [21]:
def add_point(df):
    df['geometry'] = [Point(xy) for xy in zip(df['lon_centroid'], 
                                              df['lat_centroid'])]
    
    return df 

All_GFW_Grid = All_GFW_Grid.map_partitions(add_point)

In [36]:
first_part = All_GFW_Grid.compute().head()

In [52]:
def convert_to_hexagon(df):
    x = df[['lat_centroid', 'lon_centroid']].values.tolist()
    l = []
    for i in x:
        l.append(h3.geo_to_h3(i[0], i[1], RESOLUTION))
    return l
        
All_GFW_Grid['h3'] = All_GFW_Grid.map_partitions(convert_to_hexagon)

In [53]:
def convert_to_hexagon(df):
    x = df[['Latitude', 'Longitude']].values.tolist()
    l = []
    for i in x:
        l.append(h3.geo_to_h3(i[0], i[1], RESOLUTION))
    return l
        
Beneath_The_Waves_Sensor['h3'] = Beneath_The_Waves_Sensor.map_partitions(convert_to_hexagon)

In [73]:
def convert_to_hexagon(df):
    x = df[['lat', 'lon']].values.tolist()
    l = []
    for i in x:
        l.append(h3.geo_to_h3(i[0], i[1], RESOLUTION))
    return l
        
Beneath_the_Waves['h3'] = Beneath_The_Waves.map_partitions(convert_to_hexagon)

In [74]:
intersections = dd.merge(All_GFW_Grid, Beneath_the_Waves, on='h3').compute()

date  lat_bin  lon_bin       mmsi  fishing_hours  \
0    2018-08-02 00:00:00 UTC     40.4    -69.4  368008410      14.129583   
1    2018-08-02 00:00:00 UTC     40.8    -67.7  367316510       3.068056   
2    2018-08-02 00:00:00 UTC     40.8    -67.7  367316510       3.068056   
3    2018-08-02 00:00:00 UTC     40.8    -67.7  367085960      13.184861   
4    2018-08-02 00:00:00 UTC     40.8    -67.7  367085960      13.184861   
5    2018-08-02 00:00:00 UTC     40.8    -67.7  367707030      16.779583   
6    2018-08-02 00:00:00 UTC     40.8    -67.7  367707030      16.779583   
7    2018-08-02 00:00:00 UTC     41.5    -69.8  338185508       1.932500   
8    2018-08-02 00:00:00 UTC     41.5    -69.8  338203701       0.837222   
9    2018-08-02 00:00:00 UTC     41.5    -69.8  338229321       2.733194   
10   2018-08-02 00:00:00 UTC     41.5    -69.8  338126698       1.253611   
11   2018-08-02 00:00:00 UTC     41.5    -69.8  338132083       0.917361   
12   2018-08-02 00:00:00 UTC     41.5    -69.8  338130603       2.181806   
13   2018-08-02 00:00:00 UTC     41.6    -69.9  338185508       2.825417   
14   2018-08-02 00:00:00 UTC     41.6    -69.9  338203701       0.287639   
15   2018-08-02 00:00:00 UTC     41.6    -69.9  338229321       2.625417   
16   2018-08-02 00:00:00 UTC     41.6    -69.9  338132083       2.480833   
17   2018-08-02 00:00:00 UTC     41.6    -69.9  338130603       1.944028   
18   2018-08-02 00:00:00 UTC     41.6    -69.8  338185508       0.299722   
19   2018-08-02 00:00:00 UTC     41.6    -69.8  338185508       0.299722   
20   2018-08-02 00:00:00 UTC     41.6    -69.8  338185508       0.299722   
21   2018-08-02 00:00:00 UTC     41.6    -69.8  338229321       0.916528   
22   2018-08-02 00:00:00 UTC     41.6    -69.8  338229321       0.916528   
23   2018-08-02 00:00:00 UTC     41.6    -69.8  338229321       0.916528   
24   2018-08-02 00:00:00 UTC     41.6    -69.8  338126698       0.591250   
25   2018-08-02 00:00:00 UTC     41.6    -69.8  338126698       0.591250   
26   2018-08-02 00:00:00 UTC     41.6    -69.8  338126698       0.591250   
27   2018-08-02 00:00:00 UTC     41.6    -69.8  338132083       1.124167   
28   2018-08-02 00:00:00 UTC     41.6    -69.8  338132083       1.124167   
29   2018-08-02 00:00:00 UTC     41.6    -69.8  338132083       1.124167   
30   2018-08-02 00:00:00 UTC     41.6    -69.8  338130603       1.170139   
31   2018-08-02 00:00:00 UTC     41.6    -69.8  338130603       1.170139   
32   2018-08-02 00:00:00 UTC     41.6    -69.8  338130603       1.170139   
33   2018-08-02 00:00:00 UTC     41.9    -66.4  316012470       4.341111   
34   2018-08-02 00:00:00 UTC     42.0    -66.3  316010284       1.920694   
35   2018-08-02 00:00:00 UTC     42.0    -66.9  316012480       1.263889   
36   2018-08-02 00:00:00 UTC     42.1    -66.7  316033298       8.055417   
37   2018-08-02 00:00:00 UTC     42.1    -66.7  316025491       0.804167   
0    2018-08-03 00:00:00 UTC     40.4    -69.4  368008410       4.837500   
1    2018-08-03 00:00:00 UTC     40.8    -67.7  367316510       6.306111   
2    2018-08-03 00:00:00 UTC     40.8    -67.7  367316510       6.306111   
3    2018-08-03 00:00:00 UTC     40.8    -67.7  367707030      17.275556   
4    2018-08-03 00:00:00 UTC     40.8    -67.7  367707030      17.275556   
5    2018-08-03 00:00:00 UTC     41.2    -68.8  366866750       0.717222   
6    2018-08-03 00:00:00 UTC     41.2    -68.8  366866750       0.717222   
7    2018-08-03 00:00:00 UTC     41.5    -69.8  338185508       1.000278   
8    2018-08-03 00:00:00 UTC     41.5    -69.8  338181423       1.644722   
9    2018-08-03 00:00:00 UTC     41.5    -69.8  338229321       2.437361   
10   2018-08-03 00:00:00 UTC     41.5    -69.8  338126698       1.515972   
11   2018-08-03 00:00:00 UTC     41.5    -69.8  338132083       0.898472   
12   2018-08-03 00:00:00 UTC     41.5    -69.8  338130603       1.449167   
13   2018-08-03 00:00:00 UTC     41.5    -69.6  338222665       4.167778

In [79]:
intersections = _74

In [77]:
pd.unique(Beneath_the_Waves['ptt'])

32

## Now we create a geodataframe for the GFW points as well and call it gfwgdf

**TODO:** Update below to run efficiently


Using Dask with GeoDataFrame Howto:
+ https://towardsdatascience.com/geospatial-operations-at-scale-with-dask-and-geopandas-4d92d00eb7e8
+ https://github.com/r-shekhar/NYC-transport/blob/master/05_raw_to_dataframe/convert_bike_csv_to_parquet.py

In [38]:
#gridsgdf=gridsgdf.reset_index().rename(columns={'index':'polyindex'})
all_geo = All_GFW_Grid['geometry']

def find_intersect(df):
    gfwgdf = gpd.GeoDataFrame(df, 
                              crs=crs, 
                              geometry=all_geo)
    joindf = gpd.sjoin(gfwgdf,gridsgdf, how="inner", op="within")
    totfishhrsdf = joindf.groupby('index_right').agg({'fishing_hours':'sum'})
    totfishhrsdf = totfishhrsdf.reset_index()
    polyfishdf=pd.merge(gridsgdf,totfishhrsdf, left_on='polyindex', right_on='index_right',how='inner')
    return polyfishdf

polyfishdf = All_GFW_Grid.map_partitions(find_intersect)
gfwgdf.head()

ValueError: Metadata inference failed in `find_intersect`.

You have supplied a custom function and Dask is unable to 
determine the type of output that that function returns. 

To resolve this please provide a meta= keyword.
The docstring of the Dask function you ran should have more information.

Original error is below:
------------------------
TypeError("unhashable type: 'Point'")

Traceback:
---------
  File "/home/prafulfillment/anaconda3/envs/aionthebeach/lib/python3.7/site-packages/dask/dataframe/utils.py", line 172, in raise_on_meta_error
    yield
  File "/home/prafulfillment/anaconda3/envs/aionthebeach/lib/python3.7/site-packages/dask/dataframe/core.py", line 4941, in _emulate
    return func(*_extract_meta(args, True), **_extract_meta(kwargs, True))
  File "<ipython-input-38-50a2ad5a4f29>", line 7, in find_intersect
    geometry=all_geo)
  File "/home/prafulfillment/anaconda3/envs/aionthebeach/lib/python3.7/site-packages/geopandas/geodataframe.py", line 50, in __init__
    

In [83]:
intersections  = intersections.drop(['geometry'], axis=1)

In [84]:
intersections

date  lat_bin  lon_bin       mmsi  fishing_hours  \
0    2018-08-02 00:00:00 UTC     40.4    -69.4  368008410      14.129583   
1    2018-08-02 00:00:00 UTC     40.8    -67.7  367316510       3.068056   
2    2018-08-02 00:00:00 UTC     40.8    -67.7  367316510       3.068056   
3    2018-08-02 00:00:00 UTC     40.8    -67.7  367085960      13.184861   
4    2018-08-02 00:00:00 UTC     40.8    -67.7  367085960      13.184861   
5    2018-08-02 00:00:00 UTC     40.8    -67.7  367707030      16.779583   
6    2018-08-02 00:00:00 UTC     40.8    -67.7  367707030      16.779583   
7    2018-08-02 00:00:00 UTC     41.5    -69.8  338185508       1.932500   
8    2018-08-02 00:00:00 UTC     41.5    -69.8  338203701       0.837222   
9    2018-08-02 00:00:00 UTC     41.5    -69.8  338229321       2.733194   
10   2018-08-02 00:00:00 UTC     41.5    -69.8  338126698       1.253611   
11   2018-08-02 00:00:00 UTC     41.5    -69.8  338132083       0.917361   
12   2018-08-02 00:00:00 UTC     41.5    -69.8  338130603       2.181806   
13   2018-08-02 00:00:00 UTC     41.6    -69.9  338185508       2.825417   
14   2018-08-02 00:00:00 UTC     41.6    -69.9  338203701       0.287639   
15   2018-08-02 00:00:00 UTC     41.6    -69.9  338229321       2.625417   
16   2018-08-02 00:00:00 UTC     41.6    -69.9  338132083       2.480833   
17   2018-08-02 00:00:00 UTC     41.6    -69.9  338130603       1.944028   
18   2018-08-02 00:00:00 UTC     41.6    -69.8  338185508       0.299722   
19   2018-08-02 00:00:00 UTC     41.6    -69.8  338185508       0.299722   
20   2018-08-02 00:00:00 UTC     41.6    -69.8  338185508       0.299722   
21   2018-08-02 00:00:00 UTC     41.6    -69.8  338229321       0.916528   
22   2018-08-02 00:00:00 UTC     41.6    -69.8  338229321       0.916528   
23   2018-08-02 00:00:00 UTC     41.6    -69.8  338229321       0.916528   
24   2018-08-02 00:00:00 UTC     41.6    -69.8  338126698       0.591250   
25   2018-08-02 00:00:00 UTC     41.6    -69.8  338126698       0.591250   
26   2018-08-02 00:00:00 UTC     41.6    -69.8  338126698       0.591250   
27   2018-08-02 00:00:00 UTC     41.6    -69.8  338132083       1.124167   
28   2018-08-02 00:00:00 UTC     41.6    -69.8  338132083       1.124167   
29   2018-08-02 00:00:00 UTC     41.6    -69.8  338132083       1.124167   
30   2018-08-02 00:00:00 UTC     41.6    -69.8  338130603       1.170139   
31   2018-08-02 00:00:00 UTC     41.6    -69.8  338130603       1.170139   
32   2018-08-02 00:00:00 UTC     41.6    -69.8  338130603       1.170139   
33   2018-08-02 00:00:00 UTC     41.9    -66.4  316012470       4.341111   
34   2018-08-02 00:00:00 UTC     42.0    -66.3  316010284       1.920694   
35   2018-08-02 00:00:00 UTC     42.0    -66.9  316012480       1.263889   
36   2018-08-02 00:00:00 UTC     42.1    -66.7  316033298       8.055417   
37   2018-08-02 00:00:00 UTC     42.1    -66.7  316025491       0.804167   
0    2018-08-03 00:00:00 UTC     40.4    -69.4  368008410       4.837500   
1    2018-08-03 00:00:00 UTC     40.8    -67.7  367316510       6.306111   
2    2018-08-03 00:00:00 UTC     40.8    -67.7  367316510       6.306111   
3    2018-08-03 00:00:00 UTC     40.8    -67.7  367707030      17.275556   
4    2018-08-03 00:00:00 UTC     40.8    -67.7  367707030      17.275556   
5    2018-08-03 00:00:00 UTC     41.2    -68.8  366866750       0.717222   
6    2018-08-03 00:00:00 UTC     41.2    -68.8  366866750       0.717222   
7    2018-08-03 00:00:00 UTC     41.5    -69.8  338185508       1.000278   
8    2018-08-03 00:00:00 UTC     41.5    -69.8  338181423       1.644722   
9    2018-08-03 00:00:00 UTC     41.5    -69.8  338229321       2.437361   
10   2018-08-03 00:00:00 UTC     41.5    -69.8  338126698       1.515972   
11   2018-08-03 00:00:00 UTC     41.5    -69.8  338132083       0.898472   
12   2018-08-03 00:00:00 UTC     41.5    -69.8  338130603       1.449167   
13   2018-08-03 00:00:00 UTC     41.5    -69.6  338222665       4.167778

**TODO:** Update using Dask 

Links for inspiration:
+ https://github.com/rapidsai/cuxfilter
+ https://medium.com/rapids-ai/accelerating-cross-filtering-with-cudf-3b4c29c89292

In [87]:
from keplergl import KeplerGl

map_2_config = {'version': 'v1',
 'config': {'visState': {'filters': [{'dataId': 'gfwgdf',
     'id': 'vdp9dnem',
     'name': 'date',
     'type': 'timeRange',
     'value': [1325894400000, 1337040000000],
     'enlarged': True,
     'plotType': 'histogram',
     'yAxis': None}],
   'layers': [{'id': '0l5dv4',
     'type': 'geojson',
     'config': {'dataId': 'gfwgdf',
      'label': 'gfwgdf',
      'color': [18, 147, 154],
      'columns': {'geojson': 'geometry'},
      'isVisible': True,
      'visConfig': {'opacity': 0.8,
       'thickness': 0.5,
       'strokeColor': None,
       'colorRange': {'name': 'Global Warming',
        'type': 'sequential',
        'category': 'Uber',
        'colors': ['#5A1846',
         '#900C3F',
         '#C70039',
         '#E3611C',
         '#F1920E',
         '#FFC300']},
       'strokeColorRange': {'name': 'Global Warming',
        'type': 'sequential',
        'category': 'Uber',
        'colors': ['#5A1846',
         '#900C3F',
         '#C70039',
         '#E3611C',
         '#F1920E',
         '#FFC300']},
       'radius': 10,
       'sizeRange': [0, 10],
       'radiusRange': [0, 50],
       'heightRange': [0, 500],
       'elevationScale': 5,
       'stroked': False,
       'filled': True,
       'enable3d': False,
       'wireframe': False},
      'textLabel': [{'field': None,
        'color': [255, 255, 255],
        'size': 18,
        'offset': [0, 0],
        'anchor': 'start',
        'alignment': 'center'}]},
     'visualChannels': {'colorField': {'name': 'fishing_hours',
       'type': 'real'},
      'colorScale': 'quantile',
      'sizeField': None,
      'sizeScale': 'linear',
      'strokeColorField': None,
      'strokeColorScale': 'quantile',
      'heightField': None,
      'heightScale': 'linear',
      'radiusField': None,
      'radiusScale': 'linear'}}],
   'interactionConfig': {'tooltip': {'fieldsToShow': {'gfwgdf': ['date',
       'mmsi',
       'fishing_hours']},
     'enabled': True},
    'brush': {'size': 0.5, 'enabled': False}},
   'layerBlending': 'normal',
   'splitMaps': []},
  'mapState': {'bearing': 0,
   'dragRotate': False,
   'latitude': -2.1627771833951913e-11,
   'longitude': 83.17504404268193,
   'pitch': 0,
   'zoom': 0.6438560764075248,
   'isSplit': False},
  'mapStyle': {'styleType': 'dark',
   'topLayerGroups': {},
   'visibleLayerGroups': {'label': True,
    'road': True,
    'border': False,
    'building': True,
    'water': True,
    'land': True,
    '3d building': False},
   'threeDBuildingColor': [9.665468314072013,
    17.18305478057247,
    31.1442867897876],
   'mapStyles': {}}}}

map_2 = KeplerGl(height=800, data={"intersections": intersections, 
                                  "beneath_the_waves": Beneath_the_Waves.compute()})
map_2

User Guide: https://github.com/keplergl/kepler.gl/blob/master/docs/keplergl-jupyter/user-guide.md


KeplerGl(data={'intersections':                         date  lat_bin  lon_bin       mmsi  fishing_hours  \
0 …